# Gaussian Processes: a versatile data science method that packs infinite dimensions

In [31]:
#HIDE

import pandas as pd
import MeteoAPI
import importlib as imp
import geopandas as gpd
import pydeck as pdk
import numpy as np
import spectra
import GPy
import itertools as itt
from scipy.stats import norm
import altair as alt
from IPython.core.display import display, HTML

#turn off pandas warnings
pd.options.mode.chained_assignment = None  # default='warn'

## Introduction

One of the most basic problems in data science goes something like this: 

> I want to fit a curve to data that is flexible enough to capture non-linear relationships (i.e. go through known data points without any error) but I also want confidence intervals for predictions at unknown points. 

Most methods give you one or the other. You can go with linear/polynomial regresssions and have confidence intervals, but they won't perfectly fit your data. Or you can go with splines, LOESS and other non-parametric methods, but then you won't get confidence intervals out of the box (you still can estimate them with bootstrapping but it's not always straightforward).

It was in this context that I learned about Gaussian Processes (GPs) first. GPs give you both a perfect interpolating function over known data points while also providing variance estimates at unknown data points. Here's a very basic (and recognizable) illustration of a GP in action.

In [32]:
#HIDE 

#random data points
X = np.array([1, 3, 4, 7, 10, 9]).reshape(-1, 1)
Y = np.array([5, 2, 2.5, 6, 5, 5]).reshape(-1, 1)

#basic GP model
illustrative_model = GPy.models.GPRegression(X=X, Y=Y, kernel=GPy.kern.Matern52(input_dim=1))
illustrative_model.optimize_restarts(num_restarts=10, verbose=False)

#prediction space & predictions
X_space = np.linspace(0, 10, 100).reshape(-1, 1)
preds = illustrative_model.predict(X_space)
Y_means = preds[0]
Y_vars = preds[1]

predictions = pd.DataFrame(np.hstack([X_space, Y_means, Y_vars]), columns=["X", "Y", "variance"])
predictions['min'] = predictions['Y'] - np.sqrt(predictions['variance'].values) * 1.95
predictions['max'] = predictions['Y'] + np.sqrt(predictions['variance'].values) * 1.95

In [33]:
#HIDE 

points = alt.Chart(pd.DataFrame(np.hstack([X, Y]), columns=["X", "Y"])).mark_point().encode(
    x="X",
    y=alt.Y("Y", scale=alt.Scale(domain=[0, 10]))
) 

line = alt.Chart(predictions).mark_line(color="black", strokeDash=[1, 2]).encode(
    x="X",
    y="Y"
)

area = alt.Chart(predictions).mark_area(opacity=0.2, color="red").encode(
    x="X",
    y="min",
    y2="max"
)

(points + line + area).properties(title = "Gaussian Process in action", width=600).configure_axis(grid=False, title="")

alt.LayerChart(...)

Once I learned about Gaussian processes, I started seeing references to them everywhere. Want to optimize hyperparameters? GPs can help. Reading an academic paper doing some cool stuff? Oh look, GPs are involved, too. That's how I decided to spend some more time to understand them (a bit better), and they did not disappoint. 

Cool stuff is meant to be shared, and that is how this post/notebook was born. In it, you will find:

0. Brief intro into how GPs work
1. GP regression as a way to interpolate in multi-dimensional space 
2. Importance of kernels in GPs
3. GPs for time-series forecasting
4. GP regressions with multiple output variables 🤯
5. GP regressions as surrogate functions and Bayesian optimization

Be forewarned: it's a loooong one!

## Data used in this notebook

One of the earliest applications of Gaussian Process is known as kriging, named after Danie G. Krige, a mining enginner from South Africa. Staying close to the roots, this notebook uses weather forecasts in Lithuania to illustrate GPs (and it makes for pretty charts, too!). An extract of the dataset is displayed below. This notebook uses [GPy](https://gpy.readthedocs.io/en/deploy/) library. If you are reading it in post format, some of the code cells are excluded for brevity. You can find the entire notebook and associated data on [GitHub](https://github.com/kamicollo/gaussian-process-intro).

In [34]:
#HIDE 

def collect_data():

    imp.reload(MeteoAPI)

    #Setup the API object
    meteoApi = MeteoAPI.MeteoAPI(use_cache = True, cache_dir = "meteo-cache")  

    #Get all available places
    places = meteoApi.get_places()

    #Get all forecasts and save as a single dataframe
    all_forecasts = [meteoApi.get_forecast(p) for p in places] 
    merged_forecasts = pd.concat(all_forecasts)

    #remove columns that are not interesting for us
    drop_cols = ['seaLevelPressure', 'relativeHumidity', 'windDirection', 'windGust', 'conditionCode']
    forecasts = merged_forecasts.drop(drop_cols, axis=1)
    
    #clip to Lithuania's borders and save
    lithuania = gpd.read_file('lt-shapefile/lt.shp')
    lt_forecasts = gpd.clip(forecasts, lithuania).reset_index(drop=True)
    lt_forecasts.to_file("lt_forecasts.geojson", driver='GeoJSON', index=False)

#collect_data()

In [35]:
#read in weather forecasts and Lithuania's shape file
lt_forecasts = gpd.read_file("lt_forecasts.geojson")
lithuania = gpd.read_file('lt-shapefile/lt.shp')
lt_forecasts.head(n=5)

forecastTimeUtc  airTemperature  windSpeed  cloudCover  \
0  2022-02-01T06:00:00            -2.8        4.0        18.0   
1  2022-02-04T21:00:00             1.7        5.0       100.0   
2  2022-02-06T18:00:00             2.4        7.0        97.0   
3  2022-02-06T12:00:00             2.1        5.0       100.0   
4  2022-02-06T06:00:00             0.3        7.0       100.0   

   totalPrecipitation        location                   geometry  
0                 0.0  Senoji Radiškė  POINT (23.25380 54.29488)  
1                 1.2  Senoji Radiškė  POINT (23.25380 54.29488)  
2                 3.5  Senoji Radiškė  POINT (23.25380 54.29488)  
3                 1.0  Senoji Radiškė  POINT (23.25380 54.29488)  
4                 0.9  Senoji Radiškė  POINT (23.25380 54.29488)

## How do GPs work? 

Parametric algorithms typically fit a fixed number of parameters to data (think linear regression and its coefficients). Non-parametric methods, on the other hand, typically use data points themselves as "parameters" (think K-nearest neighbours where classification depends solely on existing data points). 

Gaussian Processes fall somewhere in between. Instead of fitting a fixed number of parameters, they fit a distribution of _functions_ to data, where these functions are drawn from a multivariate normal distribution (which is what enables having confidence intervals out of the box), while the functions themselves are additionally parameterized by existing data points. That's not an easy to digest sentence, I know... One of the best definitions I found is from Julia's GP package:

> Gaussian processes are a family of stochastic processes which provide a flexible nonparametric tool for modelling data. A Gaussian Process places a prior over functions, and can be described as an infinite dimensional generalisation of a multivariate Normal distribution. Moreover, the joint distribution of any finite collection of points is a multivariate Normal. This process can be fully characterised by its mean and covariance functions, where the mean of any point in the process is described by the mean function and the covariance between any two observations is specified by the kernel. Given a set of observed real-valued points over a space, the Gaussian Process is used to make inference on the values at the remaining points in the space.

In some ways, GPs thus incorporate both parametric and non-parametric worlds - they have fixed parameters (the mean and the variance of the prior), but they also use data as parameters (as the posterior of the functions is effectively drawn from n-dimensional Gaussian distribution, where n is the number of sample points). 

If you are interested to understand GPs deeper (and I definitely suggest that), I highly recommend [a tutorial on YouTube by Richard Turner](https://www.youtube.com/watch?v=92-98SYOdlY) and [a visual exploration of Gaussian processes by three researchers from University of Konstanz](https://distill.pub/2019/visual-exploration-gaussian-processes/). 

Finally, I cannot leave out two wonderful memes by [Richard McElreath](https://twitter.com/rlmcelreath)...

In [36]:
#HIDE 

display(HTML("""
<blockquote class="twitter-tweet"><p lang="en" dir="ltr">help <a href="https://t.co/wbDo3CqpTK">pic.twitter.com/wbDo3CqpTK</a></p>&mdash; Richard McElreath 🦔 (@rlmcelreath) <a href="https://twitter.com/rlmcelreath/status/1495734508192215045?ref_src=twsrc%5Etfw">February 21, 2022</a></blockquote> <script async src="https://platform.twitter.com/widgets.js" charset="utf-8"></script> 
"""))

If you are wondering how one can fit a "infinite-dimensional" normal distribution, the answer lies in the fact that a marginal distribution of a normal distribution is normal, just like is a joint and a conditional distribution of two normal distributions. Richard Turner does a really great job at illustrating these dynamics in his tutorial. If you don't watch it now, make sure at least to put it in your bookmarks/open tabs list - it's a really good one!

For all their coolness, GPs Achilles heel is computational complexity. They scale with amount of data as any other non-parametric methods, with most implementations having $O(n^3)$. Improving that is an active line of research, whereas for every day data scientists concerned with speed can choose between GPU-enabled [GPyTorch](https://gpytorch.ai/) and efficiency focused [celerite](https://celerite.readthedocs.io/en/stable/python/benchmark/) libraries. Just keep in mind that GPs are not really an option if you have 1,000,000s of observations.

## 1. Gaussian Process Regression - interpolations

Let's start with the classical application of Gaussian Process in geostatistics. Imagine you are building an application that requires knowing air temperature at any given location in Lithuania. What you have, though, is just the measurements at weather stations. Here's how it looks visually.

In [37]:
#HIDE

#pick a single forecast time
fc_time = lt_forecasts.loc[0, 'forecastTimeUtc']
morning_forecast = lt_forecasts[lt_forecasts['forecastTimeUtc'] == fc_time].reset_index(drop=True)

In [38]:
#HIDE 

#determine initial map view
bounds = morning_forecast.total_bounds
lt_view = pdk.ViewState(latitude=(bounds[1] + bounds[3]) / 2, longitude=(bounds[0] + bounds[2]) / 2, zoom=6)

colors = ["#d7191c", "#ffffbf", "#1a9641"]

#create helper columns in dataframe for coloring purposes
colorscale = spectra.scale(colors)
temperatures = morning_forecast['airTemperature'].values
scaled_temps = (temperatures - np.min(temperatures)) / (np.max(temperatures) - np.min(temperatures))
scaled_colors = [[c * 255 for c in colorscale(t).clamped_rgb] for t in scaled_temps]
morning_forecast['color'] = scaled_colors

#create the point layer and visualize
point_layer = pdk.Layer("ScatterplotLayer", morning_forecast,
    pickable=True, filled=True, radius_min_pixels=2,
    get_position="geometry.coordinates",
    get_radius="airTemperature",
    get_fill_color='color',        
)

tooltip = "{location}\nTemperature: {airTemperature}\n Wind speed: {windSpeed}"
sc_plot = pdk.Deck(layers=[point_layer], tooltip={"text": tooltip}, initial_view_state=lt_view)
sc_plot.to_html()


Let's use Gaussian Process regression to interpolate. We will fit a GP using coordinates as features and air temperature as the dependent variable.

In [39]:
#organize data into predictors and independent variables
coordinates = np.zeros((len(morning_forecast),2))
coordinates[:,0] = morning_forecast.geometry.x.values
coordinates[:,1] = morning_forecast.geometry.y.values

actual_temperatures = morning_forecast['airTemperature'].values.reshape(-1, 1)

#fit the simplest GP model with default parameters
interpolation_model = GPy.models.GPRegression(X=coordinates, Y=actual_temperatures)
interpolation_model.optimize_restarts(num_restarts = 1, verbose=False)

#define the grid covering Lithuania
x_space = np.linspace(coordinates[:,0].min(), coordinates[:,0].max(), 100)
y_space = np.linspace(coordinates[:,1].min(), coordinates[:,1].max(), 100)
xx, yy = np.meshgrid(x_space, y_space)
grid = np.concatenate((xx.reshape(-1,1), yy.reshape(-1, 1)), axis=1)

#obtain predictions over the grid - GPY returns both mean and variance
p_means, p_vars = interpolation_model.predict(grid)

And, here it is - now we have predictions over the entire country. Looks pretty, doesn't it?

In [40]:
#HIDE 

#collect predictions into a GeoPandas dataframe
points = gpd.points_from_xy(grid[:,0], grid[:,1], crs='EPSG:4326')
interpolated = gpd.GeoDataFrame(p_means, columns=['temp'], geometry=points)
interpolated['scaled_temp'] = (p_means - p_means.min()) / (p_means.max() - p_means.min())
lt_interpolated = gpd.clip(interpolated, lithuania).reset_index(drop=True)

#plot as a heatmap
heatLayer = pdk.Layer(
    'HeatmapLayer', 
    lt_interpolated,
    opacity=0.5,
    get_position="geometry.coordinates",
    aggregation=pdk.types.String("MEAN"),
    color_range=[[c*255 for c in colorscale(i).clamped_rgb] for i in [0,0.5,1]],
    threshold=1,
    get_weight="scaled_temp",
    pickable=False,
)

r = pdk.Deck(layers=[heatLayer,point_layer], initial_view_state=lt_view, tooltip={"text": "Location: {location} \n Temperature: {airTemperature}"})
r.to_html()

### But how good is it?

Pretty, sure, but are these predictions any good? Let's test it out. I will split the dataset into a train and a test set and measure the prediction accuracy by mean absolute error (MAE).

In [41]:
#split the dataset 

from sklearn.model_selection import train_test_split as tts
from sklearn.metrics import mean_absolute_error
train_coords, test_coords, train_temps, test_temps = tts(coordinates, actual_temperatures, random_state=42)

#small helper function to get training and test set errors
def get_errors(models, X_train, X_test, Y_train, Y_test):
    results = []
    for label, model in models.items():
        training_error = mean_absolute_error(Y_train, model.predict(X_train)[0])
        test_error = mean_absolute_error(Y_test, model.predict(X_test)[0])
        results.append((label, training_error, test_error))
    return pd.DataFrame(results, columns=['model', 'Training MAE', 'Test MAE'])

In [42]:
#let's create an initial model and test its accuracy
models = {
    'basic-GP': GPy.models.GPRegression(X=train_coords, Y=train_temps)
}

models['basic-GP'].optimize_restarts(num_restarts=1, verbose=False)

get_errors(models, train_coords, test_coords, train_temps, test_temps)

model  Training MAE  Test MAE
0  basic-GP      0.095522  0.122836

Looks pretty good to me! It's off by 0.1 degree (Celsius) on average in a dataset where temperature ranges from $-7.9$ to $-0.3$ degrees. 

What is somewhat confusing is that its training error is not zero. GPs are interpolating functions, so this should only happen when there are multiple observations at the same input points (in which case the default GP kernel would end up predicting the mean of the observations), and there are no such cases in the dataset we are looking at. I suspect that this happens either because of numerical artifacts in the fitting process or there may be very sharp differences in temperature in nearby locations that the default GP kernel is not able to perfectly capture. Conceptually, that number should be zero, though.

So far, we looked only at mean predictions. Remember that one of the unique aspects of a Gaussian Process is that we also get confidence (variance) over the predictions. Let's see how accurate the confidence intervals are.

In [43]:
#get predictions for the test set
test_means, test_vars = models['basic-GP'].predict(test_coords)

#list of confidence intervals of interest
conf_ints = pd.DataFrame([0.5, 0.7, 0.9, 0.95, 0.99], columns=['confidence level'])
conf_ints['total observations'] = len(test_means)

#helper to find # of observations falling into a confidence interval
def count_in_range(cint):
    factor =  -norm.ppf((1 - cint) / 2)
    side_range = np.sqrt(test_vars) * factor
    return np.sum((test_temps <= (test_means + side_range)) & (test_temps >= (test_means - side_range)))
    
#calculate them all
conf_ints['observations in interval'] = conf_ints['confidence level'].apply(count_in_range)
conf_ints['% observations in interval'] = \
    conf_ints['observations in interval'] / conf_ints['total observations']
conf_ints

confidence level  total observations  observations in interval  \
0              0.50                 513                       290   
1              0.70                 513                       393   
2              0.90                 513                       479   
3              0.95                 513                       495   
4              0.99                 513                       509   

   % observations in interval  
0                    0.565302  
1                    0.766082  
2                    0.933723  
3                    0.964912  
4                    0.992203

It seems that in our case, the confidence intervals produced by Gaussian Process are actually even conservative!

## 2. Kernels in Gaussian Processes

You may have noticed that I have used all defaults of the [GPy regresssion module](https://gpy.readthedocs.io/en/deploy/GPy.models.html#module-GPy.models.gp_regression), and may be curious if an even better performance may be achieved by tuning some of the hyperparameters. By far the most important hyperparameter in Gaussian Processes is the kernel function that defines the correlation between two data points (the default is the radial basis function, $R(h) = e^{-\theta h^2}$). GPy has a number of kernels implemented, and even allows defining custom kernels. They have an [entire notebook](https://nbviewer.org/github/SheffieldML/notebook/blob/master/GPy/basic_kernels.ipynb) dedicated to exploring kernels which is definitely worthwhile skimming through.

Let's see what we can achieve in our interpolation task by using other kernels. Specifically, let's try out:
 - Matern52 kernel (Matern kernels are a generalization of RBF kernels with an additional smoothing parameter)
 - A combination of Matern52 and a linear kernel. I choose this particular combination by reasoning that there may be a linear temperature trend across latitude/longitude that may be worth trying to capture.

In [14]:
matern_kernel = GPy.kern.Matern52(input_dim=2)
linear_kernel = GPy.kern.Linear(input_dim=2)

models['Matern52 kernel'] = GPy.models.GPRegression(X=train_coords, Y=train_temps, kernel = matern_kernel)
models['Matern52 kernel'].optimize_restarts(num_restarts=1, verbose=False)

models['Matern52 + linear kernel'] = GPy.models.GPRegression(
    X=train_coords, Y=train_temps, kernel = matern_kernel + linear_kernel
)
models['Matern52 + linear kernel'].optimize_restarts(num_restarts=1, verbose=False)

get_errors(models, train_coords, test_coords, train_temps, test_temps)

model  Training MAE  Test MAE
0                  basic-GP      0.095522  0.122836
1           Matern52 kernel      0.055417  0.099285
2  Matern52 + linear kernel      0.044996  0.097688

And, indeed - the performance is better; using kernels allowed reducing test MAE by 20%. So, if there is one thing to remember - make sure to test different kernels (and see if you can reason what kernel combinations may be most appropriate given your data).

## 3. Forecasting with GPs

The flexibility of kernel functions is what makes GPs useful for time series forecasting, too. However, you won't get far with a default RBF kernel as its predictions converge to zero (or mean, if a bias kernel is added) very quickly once you step out of a domain observed during training. Here's an illustration using the 1D example from earlier.

In [15]:
#HIDE 

#prediction space & predictions
X_space = np.linspace(0, 20, 100).reshape(-1, 1)
preds = illustrative_model.predict(X_space)
Y_means = preds[0]
Y_vars = preds[1]

predictions = pd.DataFrame(np.hstack([X_space, Y_means, Y_vars]), columns=["X", "Y", "variance"])
predictions['min'] = predictions['Y'] - np.sqrt(predictions['variance'].values) * 1.95
predictions['max'] = predictions['Y'] + np.sqrt(predictions['variance'].values) * 1.95

points = alt.Chart(pd.DataFrame(np.hstack([X, Y]), columns=["X", "Y"])).mark_point().encode(
    x="X",
    y=alt.Y("Y", scale=alt.Scale(domain=[0, 10]))
) 

line = alt.Chart(predictions).mark_line(color="black", strokeDash=[1, 2]).encode(
    x="X",
    y="Y"
)

area = alt.Chart(predictions).mark_area(opacity=0.2, color="red", clip=True).encode(
    x="X",
    y="min",
    y2="max"
)

(points + line + area) \
    .properties(title = "RBF kernel predictions out of observed domain", width=600) \
    .configure_axis(grid=False, title="")

alt.LayerChart(...)

I will illustrate a better way to do it using one of the city temperature forecasts. We will take the first 48 hours of predictions in one of the Lithuanian cities and see if we can generate a reasonable forecast for it.

In [16]:
#get the relevant data for Kaunas forecast
point_forecast = lt_forecasts[lt_forecasts['location'] == "Kaunas"]
point_forecast['forecastTimeUtc'] = pd.to_datetime(point_forecast['forecastTimeUtc'])
point_forecast['hours_offset'] = (point_forecast['forecastTimeUtc'] - point_forecast['forecastTimeUtc'].min()).astype("timedelta64[h]")
point_forecast = point_forecast.sort_values(['forecastTimeUtc'])
first_two_days = point_forecast.head(48)

alt.Chart(first_two_days).mark_line().encode(
    x = alt.X("yearmonthdatehours(forecastTimeUtc):O", title="Time"),
    y = "airTemperature"
).properties(
    title="48-hour temperature forecast in Kaunas",
    width=600
)


alt.Chart(...)

Given the cyclical nature of temperature during a day, let's use a periodic exponential kernel combined with a linear kernel that should capture the day-over-day trend.

Here's the initial result.

In [17]:
#HIDE 

#helper plotting function
def plot_temp_forecast(model):

    hours = np.fromiter(range(0,80), float).reshape(-1, 1)
    predicted_mean, predicted_var = model.predict(hours)

    temp_forecasts = pd.DataFrame({
        'hours': hours.reshape(-1),
        'temperature' : predicted_mean.reshape(-1),
        'variance': predicted_var.reshape(-1)
    })

    temp_forecasts['lower'] = temp_forecasts['temperature'] - np.sqrt(temp_forecasts['variance']) * 1.96
    temp_forecasts['upper'] = temp_forecasts['temperature'] + np.sqrt(temp_forecasts['variance']) * 1.96
    fact_chart = alt.Chart(first_two_days).mark_line().encode(
        x=alt.X('hours_offset', title="hours"),
        y=alt.Y('airTemperature', title="temperature")
    ) 

    forecast_chart = alt.Chart(temp_forecasts).mark_line(color='red').encode(
        x=alt.X('hours', title="hours"),
        y=alt.Y('temperature', title="temperature")
    )

    forecast_confidence = alt.Chart(temp_forecasts).mark_area(color='red', opacity=0.2).encode(
        x=alt.X('hours', title="hours"),
        y=alt.Y('lower', title="temperature"),
        y2=alt.Y2('upper', title="temperature")
    )

    return (fact_chart + forecast_chart + forecast_confidence).properties(title="Temperature forecast")

In [45]:
#get the variables
hours_offset = first_two_days['hours_offset'].values.reshape(-1, 1)
temperature = first_two_days['airTemperature'].values.reshape(-1, 1)

#run the prediction
forecast_kernel = (GPy.kern.PeriodicExponential(input_dim=1) + GPy.kern.Linear(input_dim=1) + GPy.kern.Bias(input_dim=1))
forecast_model = GPy.models.GPRegression(X=hours_offset, Y=temperature, kernel = forecast_kernel, normalizer=True)
forecast_model.optimize_restarts(num_restarts=1, verbose=False)

plot_temp_forecast(forecast_model)

alt.LayerChart(...)

The predictions appear quite reasonable - GP definitely picked up the cyclical trends and there seem to be a linear downwards trend, too. But there's something fishy. We see that GPs (again!) do not perfectly interpolate existing data. Furthermore, what is with the variances? They seem to be constant over time which is weird, too. What is going on?

In this case, the answer is that the GP optimization process is stochastic, and a single attempt did not yield good results. If we rerun the optimization process multiple (say, 20) times, we will see different results (see below). This is another take away about GPs - in most cases, you may need to re-initialize the fitting process multiple times to get what you are looking for. 

At the same time, looking below you may reasonably ask: is this not overfitting? I would tend to agree, actually! How do you go about reducing overfitting if you have that problem? Recall that GPs are defined over a prior of functions - it is possible to provide stronger priors as well as introduce constraints over some of the fitting parameters. I haven't tried it out myself, but if you are interested, you can find more detail in [one of the GPy tutorials](https://nbviewer.org/github/SheffieldML/notebook/blob/master/GPy/models_basic.ipynb).

In [48]:
#rerun optimization 20 times
forecast_model.optimize_restarts(num_restarts=20, verbose=False)

plot_temp_forecast(forecast_model)

 /home/aurimas/apps/anaconda3/envs/gp-processes/lib/python3.8/site-packages/paramz/transformations.py:111: RuntimeWarning:overflow encountered in expm1
 /home/aurimas/apps/anaconda3/envs/gp-processes/lib/python3.8/site-packages/GPy/kern/src/periodic.py:86: RuntimeWarning:overflow encountered in true_divide
 /home/aurimas/apps/anaconda3/envs/gp-processes/lib/python3.8/site-packages/GPy/kern/src/periodic.py:40: RuntimeWarning:invalid value encountered in multiply
 /home/aurimas/apps/anaconda3/envs/gp-processes/lib/python3.8/site-packages/GPy/kern/src/periodic.py:40: RuntimeWarning:invalid value encountered in cos


alt.LayerChart(...)

## GPs and multiple dependent variables 🤯

Another cool aspect of Gaussian Processes is that they can model relationships between multiple output variables. I have to admit that the maths behind how it works exactly is beyond me, though I suspect it must have to do with the fact that a joint distribution of multiple normal distributions is a normal distribution, so one can model the joint distribution as a single output and then marginalize it as needed.

Continuing with the weather data examples, here's an application to consider: Suppose that, due to historical reasons, not all stations can measure temperature and wind speed simultaneously. The ones on the east side of the country tend to measure only temperature, and the ones to the west - only wind speed. If we wanted to build models to predict temperature and wind speed at other locations, we could simply build two models independently, using the relevant station data for each each. But we may have reason to believe that temperature and wind speed are related, and capturing that relationship in the model may be beneficial. Let's see if that is the case.

Below is a visual illustration - I'll be using a subset of the weather stations in this example.

In [20]:
#let's use 25% and 75% quantiles as east/west centers
mid_lt = morning_forecast[(morning_forecast.geometry.y > 55) & (morning_forecast.geometry.y < 56)]

east_center, west_center = np.quantile(mid_lt.geometry.x.values, q=[0.2, 0.8])
sd = np.std(morning_forecast.geometry.x.values)

#use two normal distributions to generate probability densities
east_dens = norm.pdf(mid_lt.geometry.x.values, loc=east_center, scale=sd)
west_dens = norm.pdf(mid_lt.geometry.x.values, loc=west_center, scale=sd)

#normalize densities to probabilities
prob_of_east = east_dens / (east_dens + west_dens)

#sample stations 
temp_stations = mid_lt.sample(n=40, weights = prob_of_east, random_state=42)
temp_stations['type'] = 'Temperature station'
speed_stations = mid_lt.sample(n=40, weights = (1 - prob_of_east), random_state=42)
speed_stations['type'] = 'Wind speed station'

In [21]:
#HIDE 

#create the point layer and visualize
temp_layer = pdk.Layer("ScatterplotLayer", temp_stations,
    pickable=True, filled=True, radius_min_pixels=3,
    get_position="geometry.coordinates",
    get_radius=10,
    get_fill_color=[c*255 for c in colorscale(0).clamped_rgb],
)

speed_layer = pdk.Layer("ScatterplotLayer", speed_stations,
    pickable=True, filled=True, radius_min_pixels=3,
    get_position="geometry.coordinates",
    get_radius=10,
    get_fill_color=[c*255 for c in colorscale(1).clamped_rgb],
)

sc_plot = pdk.Deck(layers=[temp_layer, speed_layer], tooltip={"text": "Station type: {type}"}, initial_view_state=lt_view)
sc_plot.to_html()


In [22]:
#organize data into predictors and independent variables
y_variables = ['airTemperature', 'windSpeed']
no_y_variables = len(y_variables)

#prepare a list of coordinates/obs (kept as a list of 2)
coords = [
    np.vstack([temp_stations.geometry.x.values, temp_stations.geometry.y.values]).T,
    np.vstack([speed_stations.geometry.x.values, speed_stations.geometry.y.values]).T
]

obs = [
    temp_stations[y_variables[0]].values.reshape(-1, 1),
    speed_stations[y_variables[1]].values.reshape(-1, 1),
]

test = [
    temp_stations[y_variables[1]].values.reshape(-1, 1),
    speed_stations[y_variables[0]].values.reshape(-1, 1),
]

To establish the baseline, let's first train a GP regressions for the two datasets (temperature-measuring stations and wind-measuring stations) separately and see how well the models predict the other measurement at the locations where that measurement is not available to the model (i.e. how well a model trained on wind-measuring stations fares in predicting wind speed at temperature-measuring locations and vice-versa).

In [23]:
#kernels
K1 = GPy.kern.Bias(2)
K2 = GPy.kern.Linear(2)
K3 = GPy.kern.Matern32(2)

#train independent models
result_bag = []
kernel = K1 + K3 * K2
for i, name in enumerate(y_variables):
    j = 0 if i == 1 else 1    
    train_x = coords[i]    
    train_y = obs[i]
    test_x = coords[j]
    test_y = test[j]
    singleOutput_model = GPy.models.GPRegression(X=train_x, Y=train_y, kernel=kernel)
    singleOutput_model.optimize_restarts(num_restarts=1, verbose=False)
    preds = singleOutput_model.predict(test_x)
    test_error = mean_absolute_error(test_y, preds[0])
    error_var = np.var(test_y - preds[0]) 
    result_bag.append((name, 'single-output', test_error, error_var))
    
pd.DataFrame(result_bag, columns=['Variable', 'Model type', 'Mean absolute error', 'Error variance'])

Variable     Model type  Mean absolute error  Error Variance
0  airTemperature  single-output             0.958267        1.321167
1       windSpeed  single-output             0.539025        0.498869

We can see that the erorrs are not too bad, actually. Can a multi-output GP regression do better?

The GPy model type to be used for such scenarios is `GPCoregionalizedRegression`, and it has a somewhat different API than most of the other GPy models (you need to pass inputs as list for each of the output variable; predictions require an extra index column in the input array). I based the code below on [their dedicated tutorial for coregionalized regressions](https://nbviewer.org/github/SheffieldML/notebook/blob/master/GPy/coregionalized_regression_tutorial.ipynb).

In [24]:
#Define a multi-output kernel
icm = GPy.util.multioutput.LCM(input_dim=2, num_outputs=2, kernels_list=[K1, K2, K3])

#Setup the model and optimize
multiOutput_model = GPy.models.GPCoregionalizedRegression(X_list=coords, Y_list=obs, kernel = icm)
multiOutput_model.optimize_restarts(num_restarts=5, verbose=False)

#Setup the array used for predictions; it uses an extra column to indicate output index to predict
inds = np.ones((coords[0].shape[0], 1))
predSpace = np.vstack([np.hstack([coords[0 if i == 1 else 1], inds * i]) for i in range(no_y_variables)])
noise_dict = {'output_index': predSpace[:, 2].astype(int)} 

#get all predictions and evaluate
obs_preds = multiOutput_model.predict(predSpace, Y_metadata=noise_dict)
result_bag = []
for i, name in enumerate(y_variables):
    j = 0 if i == 1 else 1
    test_y = test[j]
    pred_y = obs_preds[0][predSpace[:, 2] == i] 
    test_error = mean_absolute_error(test_y, pred_y)
    error_var = np.var(test_y - pred_y)    
    result_bag.append((name, 'multi-output', test_error, error_var))
    
pd.DataFrame(result_bag, columns=['Variable', 'Model type', 'Mean absolute error', 'Error variance'])

Variable    Model type  Mean absolute error  Error Variance
0  airTemperature  multi-output             0.868765        0.935922
1       windSpeed  multi-output             0.559075        0.537072

The results for this dataset are... interesting. In case of temperature, the model performs clearly better, but its performance is actually slightly worse for wind speeds. The thing about wind speeds, however, is that the forecasts are available only on an integer basis. So these results may simply be a factor of underlying data and shouldn't necessarily be interpreted as a "worse fit". 

And, yes, I know - one really shouldn't fit a continuous function if the output variables are count-like.. But hey, you know what - it is possible to [model Poisson-like variables with GPs](https://nbviewer.org/github/SheffieldML/notebook/blob/master/GPy/Poisson%20regression%20tutorial.ipynb) too! Maybe another time.

## GPs as surrogate functions and Bayesian optimization

So far, I explored use cases where GP is the main model we use for fitting. The flexibility of GPs, however, make them very popular candidates to be used as surrogate functions, too. 

Imagine you have a model that takes a long time to run - perhaps it is something as simple as an XGBoost classifier on a relatively large dataset, or maybe it is a complex physics simulation of the universe that takes a day to run on a supercomputer cluster. In both cases, you can only make a few runs of them with different (hyper-) parameters, and you would like to find the optimal setting of those hyperparameters (e.g. tune a learning rate for XGBoost) or use the limited outputs to interpolate in the rest of input space. 

In such scenarios, you can do the following:
 
 - Run the expensive model a few times with carefully spaced out parameter values and obtain initial observations of the dependent variable (or a loss function, in case of an ML model)
 - Then, fit a Gaussian Process over the obtained data points and treat it as an approximate (surrogate) function of the underlying model
 - Use GP predictions to infer expected values of the true underlying model at unknown locations
 - If optimization is of interest (e.g. finding XGBoost hyperparameters that lead to the best model performance), use the uncertainty of predictions (variance) to determine the next combination of parameters that are most promising to evaluate the true underlying model on. 
 - Rinse and repeat the steps above iteratively.

The iterative process of looking for an optimal value is what is also known as "exploration vs exploitation". You choose to either explore (using variance information to determine locations with highest uncertainty) or exploit (by evaluating the model at locations close to the best currently known point). There are multiple ways how to determine the next point for evaluation (i.e. how to make the exploration vs. exploitation trade-off). One of them is known as the Expected Improvement maximization approach. I won't delve into detail on it here - I highly recommend a [post by Martin Krasser on Bayesian Optimization](https://krasserm.github.io/2018/03/21/bayesian-optimization/) if you are curious about the details.

In this notebook, I won't fit XGBoost models. Instead, I will illustrate the concept with a simple task. Let's pretend our task is to find the coldest place in Lithuania as measured by chill factor (which happens to be a village called Kirmėliai, with wind chill factor of -11.58). Here's how the distribution of chill factor looks geographically; you can see it is not a convex environment, and so using gradient-based approaches is unlikely to get us to the right place.

In [25]:
#HIDE 

#calculate chill factor and add a bit of noise to calculations
rng = np.random.default_rng(seed=42)
vp = morning_forecast['windSpeed'].values ** 0.16
t = morning_forecast['airTemperature'].values
morning_forecast['windChill'] = 13.12 + 0.6215 * t - 11.37 * vp  + 0.3965 * t * vp - rng.normal(size=len(morning_forecast))
morning_forecast['norm_windChill'] = (morning_forecast['windChill'] - morning_forecast['windChill'].min()) / (morning_forecast['windChill'].max() - morning_forecast['windChill'].min())

coldest_place = morning_forecast[morning_forecast['windChill'] == morning_forecast['windChill'].min()].loc[:, ['location', 'geometry', "windChill"]]

In [26]:
#HIDE 

chill_layer = pdk.Layer(
    'HeatmapLayer', 
    morning_forecast,
    opacity=0.5,
    get_position="geometry.coordinates",
    aggregation=pdk.types.String("MEAN"),
    color_range=[[c*255 for c in colorscale(i).clamped_rgb] for i in [0,0.5,1]],
    threshold=1,      
    get_weight="norm_windChill",    
    pickable=False,
    
)


top_chill_layer = pdk.Layer("ScatterplotLayer", coldest_place,
    pickable=True, filled=True, radius_min_pixels=3,
    get_position="geometry.coordinates",
    get_radius="10",
    get_fill_color="[230,85,13]",
)

r = pdk.Deck(layers=[chill_layer, top_chill_layer], initial_view_state=lt_view, tooltip ={ "html": "{location}: {windChill}"})
r.to_html()

Instead, let's use Bayesian optimization with Gaussian processes. There are a few python packages that support Bayesian optimization, most notably [hyperopt](https://hyperopt.github.io/hyperopt/) and [pyGPGO](https://pygpgo.readthedocs.io/en/latest/). Hyperopt uses tree of Parzen estimators (TPE) as the surrogate function, however. For this illustration, I chose to go with the aptly named [BayesianOptimization](https://github.com/fmfn/BayesianOptimization) package that uses Gaussian processes and supports Expected Improvement algorithm for iterative choices.

Let's start by randomly choosing 4 points in Lithuania and evaluating the chill factor there (we'll use the nearest station measure for any given point). Then, let's explore additional 15 locations iteratively, where each subsequent location is chosen by Expected Improvement criteria using a Gaussian Process model fit on all observations collected so far.

In [27]:
#HIDE

from shapely.geometry import Point
from shapely.ops import nearest_points

all_points = morning_forecast.geometry.unary_union

#this function returns the (negative) chill factor of the nearest station for any lat/lon combination
def get_chill_factor(lat, lon):
    point = Point(lat, lon)
    nearest = nearest_points(point, all_points)[1]
    nearest_chill_factor =  morning_forecast[morning_forecast.geometry == nearest]['windChill']
    return -nearest_chill_factor.values[0]
    

In [28]:
from bayes_opt import BayesianOptimization

#set the bounds to be the bounding box of Lithuania
param_bounds = {
    'lat': (bounds[0], bounds[2]), 
    'lon': (bounds[1], bounds[3])
}

#setup the optimizer
optimizer = BayesianOptimization(f=get_chill_factor, pbounds=param_bounds, random_state=42, verbose=False)

#let's go exploring!
optimizer.maximize(init_points=4, n_iter=15, acq = 'ei', xi=0)

What are the results? Turns out we were able to find the coldest place!

In [29]:
explorations = gpd.GeoDataFrame([{'target': d['target'], 
    'lat': d['params']['lat'],
    'lon': d['params']['lon']} for d in optimizer.res])

#type conversion lat/lon to geometry column
points = [Point(lon, lat) for i,lat,lon in explorations[['lon', 'lat']].itertuples()]
explorations = explorations.assign(**{'geometry': gpd.GeoSeries(points).set_crs('EPSG:4326')})
explorations = explorations.drop(['lat', 'lon'], axis = 1)

print("Lowest chill factor found: {:.5f}".format(-explorations['target'].max()))

Lowest chill factor found: -11.58668


To get the intuition behind what happened, here's a graphical illustration of the algorithm's path. You can see how trade-offs between exploring unknown areas vs. exploiting the information collected so far about the maximum observed value changes as more and more data points are collected. Much better than any grid search!

In [30]:
#HIDE 

point_arr = [[p.x, p.y] for p in points[4:]]
path = pd.DataFrame([{"path": point_arr}])

chill_layer = pdk.Layer(
    'HeatmapLayer', 
    morning_forecast,
    opacity=0.5,
    get_position="geometry.coordinates",
    aggregation=pdk.types.String("MEAN"),
    color_range=[[c*255 for c in colorscale(i).clamped_rgb] for i in [0,0.5,1]],
    threshold=1,
    get_weight="norm_windChill",
    pickable=True,
)

exp_layer = pdk.Layer("ScatterplotLayer", explorations,
    pickable=True, filled=True, radius_min_pixels=3,
    get_position="geometry.coordinates",
    get_radius="10",
    get_fill_color="[255,255,255]"
)

best_found = pdk.Layer("ScatterplotLayer", explorations[explorations['target'] == explorations['target'].max()],
    pickable=True, filled=True, radius_min_pixels=3,
    get_position="geometry.coordinates",
    get_radius="10",
    get_fill_color="[44,162,95]"
)

path_layer = pdk.Layer(
    type="PathLayer",
    data=path,
    pickable=True,
    get_color="[255,255,255]",
    width_scale=20,
    width_min_pixels=2,
    get_path="path",
    get_width=5,
)


top_chill_layer = pdk.Layer("ScatterplotLayer", coldest_place,
    pickable=True, filled=True, radius_min_pixels=3,
    get_position="geometry.coordinates",
    get_radius="10",
    get_fill_color="[230,85,13]"
)

r = pdk.Deck(layers=[chill_layer, exp_layer, top_chill_layer, path_layer, best_found], initial_view_state=lt_view, tooltip ={ "html": "{location}: {windChill}"})
r.to_html()

## The End

If you got here - thank you for reading and I hope this journey was interesting! 

To be fair, this is just scratching the surface on what one can do with Gaussian Processes, and there are all kind of crazy interesting things out there (for example, deep Gaussian Processes, where GPs are "stacked" on top of each other thus eliminating the need to manually specify kernels...). Most of them are beyond my ability to comprehend, but perhaps they won't be for you! At the same time, having a basic understanding of GPs and their value as flexible fitting functions that provide you with confidence estimates gets you pretty far already. And they are used in the industry, too! Here's an example from [Lyft](https://eng.lyft.com/parameter-exploration-at-lyft-b9d2a1483c82) where they use Gaussian processses and Bayesian optimization to run experiments. 

On a final note, if you happen to be Lithuanian, here's an interesting fact: turns out that a Lithuanian mathematician, [Jonas Mockus](https://lt.wikipedia.org/wiki/Jonas_Mockus) was a very influential figure in Bayesian optimization space. I was pleasantly surprised to see a familiar name when researching for this post!